In [1]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

g_year = 108
g_season = 1
g_how_many_year = 3

In [2]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True)#, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'公司代號'] != u'公司代號']
    df = df[~df[u'公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [3]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',u'公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on=u'公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [4]:
df_net_income_sii = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'sii', 'NetIncome', u'稅後純益率(%)(稅後純益)/(營業收入)', '營益分析彙總表')

df_net_income_sii

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



稅後純益率(%)(稅後純益)/(營業收入)
('year:', 107)
('season:', 4)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 107)
('season:', 3)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 107)
('season:', 2)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 107)
('season:', 1)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 106)
('season:', 4)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 106)
('season:', 3)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 106)
('season:', 2)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 106)
('season:', 1)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 105)
('season:', 4)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 105)
('season:', 3)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 105)
('season:', 2)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 105)
('season:', 1)


公司代號      公司名稱 NetIncome(%)_108Q1 NetIncome(%)_107Q4 NetIncome(%)_107Q3  \
0    1101        台泥              16.68              18.17              19.00   
1    1102        亞泥              19.65              17.99              19.54   
2    1103        嘉泥              32.84              36.76              65.25   
3    1104      環球水泥              13.19              21.99              21.91   
4    1108      幸福水泥              -3.57              -6.05              -2.05   
5    1109      信大水泥              14.89              18.71              16.20   
6    1110        東泥               7.15               3.91               7.72   
7    1201      味全公司              24.65               4.47               6.25   
8    1203      味王公司              12.15              11.58              11.95   
9    1210      大成長城               2.75               3.33               3.45   
10   1215      卜蜂企業               4.95               4.69               4.24   
11   1216        統一               7.26               6.25               6.85   
12   1217       愛之味               1.66               1.45               2.19   
13   1218      泰山企業               6.10               5.88               6.97   
14   1219      福壽實業               0.51              -0.82              -1.01   
15   1220        台榮               2.46               4.10               4.48   
16   1225       福懋油               3.51               2.67               2.47   
17   1227        佳格              10.88              10.86              11.18   
18   1229      聯華實業              85.47              48.52              51.20   
19   1231      聯華食品               5.22               6.67               6.14   
20   1232       大統益               7.30               5.47               5.09   
21   1233        天仁               7.86               7.97               8.59   
22   1234        黑松               7.69               7.82               8.21   
23   1235        興泰            -769.70             183.81             305.44   
24   1236      宏亞食品               1.73               0.67              -2.56   
25   1256   鮮活果汁-KY              13.22              13.71              14.43   
26   1262     綠悅-KY             -12.74             -11.51              -9.12   
27   1301        台塑              15.36              21.51              27.13   
28   1303      南亞塑膠               7.03              15.81              18.88   
29   1304        台聚               4.32               3.08               4.43   
30   1305        華夏               5.92               8.93              11.06   
31   1307      三芳化工               3.83               3.19               3.35   
32   1308        亞聚               8.00               4.50               5.87   
33   1309      台達化工               4.24               0.96               2.31   
34   1310        台苯              11.18               7.72               9.47   
35   1312      國喬石化              11.99              12.73              15.11   
36   1313        聯成              -0.92               1.23               1.97   
37   1314       中石化               3.80              11.12              13.27   
38   1315      達新工業               0.94               9.04              14.76   
39   1316        上曜             -33.65              15.22              22.55   
40   1319        東陽               8.85               8.40               8.32   
41   1321        大洋               3.01              -1.50               0.55   
42   1323        永裕               8.30               9.63               9.53   
43   1324      地球工業              -1.28               0.11               0.45   
44   1325        恒大               5.22               6.55               6.81   
45   1326        台化              10.04              13.59              17.34   
46   1337     再生-KY             -52.43            -128.92             -44.48   
47   1338     廣華-KY               5.46               6.13               6.69   
48   1339        昭輝              15.76               9.97              13.23   
49   

In [5]:
df_net_income_otc = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'otc', 'NetIncome', u'稅後純益率(%)(稅後純益)/(營業收入)', '營益分析彙總表')

df_net_income_otc

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



稅後純益率(%)(稅後純益)/(營業收入)
('year:', 107)
('season:', 4)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 107)
('season:', 3)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 107)
('season:', 2)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 107)
('season:', 1)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 106)
('season:', 4)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 106)
('season:', 3)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 106)
('season:', 2)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 106)
('season:', 1)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 105)
('season:', 4)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 105)
('season:', 3)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 105)
('season:', 2)
稅後純益率(%)(稅後純益)/(營業收入)
('year:', 105)
('season:', 1)


公司代號    公司名稱 NetIncome(%)_108Q1 NetIncome(%)_107Q4 NetIncome(%)_107Q3  \
0    1258   其祥-KY              -1.45              -5.48              -5.52   
1    1259      安心               1.83               2.30               2.63   
2    1264      德麥              13.68              13.45              13.56   
3    1333     恩得利             -28.45             -30.32             -36.14   
4    1336      台翰               0.43               3.83               4.23   
5    1565    精華光學              23.85              24.98              25.12   
6    1566      捷邦               3.14               1.39               1.77   
7    1569      濱川               1.24               1.26               0.96   
8    1570    力肯實業               7.52              13.00              12.30   
9    1580    新麥企業               9.19              11.25              10.22   
10   1584    精剛精密              -7.39             -12.69             -10.35   
11   1586    和勤精機              -7.91               4.16               5.28   
12   1591   駿吉-KY               5.90               5.68               5.77   
13   1593      祺驊              13.76              15.08              14.48   
14   1595    川寶科技               3.13              11.19              11.53   
15   1597      直得              13.52              22.67              22.46   
16   1599     宏佳騰               9.19               8.28               7.54   
17   1742      台蠟               4.61             -23.80             -33.77   
18   1752      南光               9.40               6.58               6.89   
19   1777      生泰              20.63              19.62              19.90   
20   1781    合世生醫             -17.22              -6.23              -5.75   
21   1784    訊聯生技               8.32               4.84               5.04   
22   1785     光洋科               3.41               1.98               3.34   
23   1787     福盈科               7.20               5.73               5.75   
24   1788    杏昌生技               7.84               7.87               7.79   
25   1795    美時製藥              13.15               1.93               1.09   
26   1799      易威             -86.31             -76.10             -64.54   
27   1813     寶利徠              11.33               9.50              11.18   
28   1815    富喬工業               5.46               8.09              10.08   
29   2035    唐榮公司               4.88              -9.69              -6.19   
30   2061      風青               0.36              -1.43              -0.60   
31   2063      世鎧              15.80              15.15              15.97   
32   2064      晉椿              -1.64               2.68               2.66   
33   2066      世德               6.28               5.62               8.63   
34   2067      嘉鋼              -3.32               4.89               4.66   
35   2221    大甲永和              11.92              13.33              14.34   
36   2230      泰茂               1.42               1.79               1.85   
37   2233      宇隆              15.86              16.17              16.49   
38   2235      謚源              15.44              13.74              14.00   
39   2596    綠意開發           -1469.45              33.23              34.22   
40   2640     大車隊               9.63              12.29              12.59   
41   2641    正德海運               9.40              11.55              12.14   
42   2643      捷迅               2.28               2.70               2.51   
43   2718      晶悅               3.20              -4.82              -8.93   
44   2719     燦星旅              -5.30              -4.76              -3.27   
45   2724   富驛-KY             -16.15              -0.66              -1.77   
46   2726   雅茗-KY               7.88               4.36               5.56   
47   2729    瓦城泰統               8.78               8.20               9.29   
48   2732    六角國際               7.50               4.91               4.82   
49   2734     易飛網               1.05              -9.01              -6.40   
50   2736      高野          

In [6]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_net_income = pd.concat([df_net_income_sii,df_net_income_otc],axis=0, ignore_index=True)

df_net_income

公司代號      公司名稱 NetIncome(%)_108Q1 NetIncome(%)_107Q4 NetIncome(%)_107Q3  \
0     1101        台泥              16.68              18.17              19.00   
1     1102        亞泥              19.65              17.99              19.54   
2     1103        嘉泥              32.84              36.76              65.25   
3     1104      環球水泥              13.19              21.99              21.91   
4     1108      幸福水泥              -3.57              -6.05              -2.05   
5     1109      信大水泥              14.89              18.71              16.20   
6     1110        東泥               7.15               3.91               7.72   
7     1201      味全公司              24.65               4.47               6.25   
8     1203      味王公司              12.15              11.58              11.95   
9     1210      大成長城               2.75               3.33               3.45   
10    1215      卜蜂企業               4.95               4.69               4.24   
11    1216        統一               7.26               6.25               6.85   
12    1217       愛之味               1.66               1.45               2.19   
13    1218      泰山企業               6.10               5.88               6.97   
14    1219      福壽實業               0.51              -0.82              -1.01   
15    1220        台榮               2.46               4.10               4.48   
16    1225       福懋油               3.51               2.67               2.47   
17    1227        佳格              10.88              10.86              11.18   
18    1229      聯華實業              85.47              48.52              51.20   
19    1231      聯華食品               5.22               6.67               6.14   
20    1232       大統益               7.30               5.47               5.09   
21    1233        天仁               7.86               7.97               8.59   
22    1234        黑松               7.69               7.82               8.21   
23    1235        興泰            -769.70             183.81             305.44   
24    1236      宏亞食品               1.73               0.67              -2.56   
25    1256   鮮活果汁-KY              13.22              13.71              14.43   
26    1262     綠悅-KY             -12.74             -11.51              -9.12   
27    1301        台塑              15.36              21.51              27.13   
28    1303      南亞塑膠               7.03              15.81              18.88   
29    1304        台聚               4.32               3.08               4.43   
30    1305        華夏               5.92               8.93              11.06   
31    1307      三芳化工               3.83               3.19               3.35   
32    1308        亞聚               8.00               4.50               5.87   
33    1309      台達化工               4.24               0.96               2.31   
34    1310        台苯              11.18               7.72               9.47   
35    1312      國喬石化              11.99              12.73              15.11   
36    1313        聯成              -0.92               1.23               1.97   
37    1314       中石化               3.80              11.12              13.27   
38    1315      達新工業               0.94               9.04              14.76   
39    1316        上曜             -33.65              15.22              22.55   
40    1319        東陽               8.85               8.40               8.32   
41    1321        大洋               3.01              -1.50               0.55   
42    1323        永裕               8.30               9.63               9.53   
43    1324      地球工業              -1.28               0.11               0.45   
44    1325        恒大               5.22               6.55               6.81   
45    1326        台化              10.04              13.59              17.34   
46    1337     再生-KY             -52.43            -128.92             -44.48   
47    1338     廣華-KY               5.46               6.13               6.69   
48    1339        昭輝              15.

In [7]:
#檢查column資料型態

#df_net_income.info() #non-null object
#df_net_income.dtypes #object
#df_net_income.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
NetIncome(%)_107Q1    float64
NetIncome(%)_106Q4    float64
NetIncome(%)_106Q3    float64
NetIncome(%)_106Q2    float64
NetIncome(%)_106Q1    float64
NetIncome(%)_105Q4    float64
NetIncome(%)_105Q3    float64
NetIncome(%)_105Q2    float64
NetIncome(%)_105Q1    float64
NetIncome(%)_104Q4    float64
NetIncome(%)_104Q3    float64
NetIncome(%)_104Q2    float64
NetIncome(%)_104Q1    float64
dtype: object
'''

df_net_income = df_net_income.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_net_income.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號                    int64
公司名稱                   object
NetIncome(%)_108Q1    float64
NetIncome(%)_107Q4    float64
NetIncome(%)_107Q3    float64
NetIncome(%)_107Q2    float64
NetIncome(%)_107Q1    float64
NetIncome(%)_106Q4    float64
NetIncome(%)_106Q3    float64
NetIncome(%)_106Q2    float64
NetIncome(%)_106Q1    float64
NetIncome(%)_105Q4    float64
NetIncome(%)_105Q3    float64
NetIncome(%)_105Q2    float64
NetIncome(%)_105Q1    float64
dtype: object

In [8]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [9]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['NetIncome(%)_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['NetIncome(%)_{0}Q{1}'.format(year, season)])
        previous_value = float(row['NetIncome(%)_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [10]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['NetIncome(%)_{0}Q{1}'.format(year, season)]) == True):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [11]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_net_income['Growth_{0}Q{1}'.format(year, season)] = df_net_income.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [12]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_net_income['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_net_income.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [13]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True)#, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'有價證券代號及名稱'] != u'股票']
    df = df[~df[u'有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df[u'產業別'] > '0']
    del newdf[u'國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf[u'備註']

    df2=newdf[u'有價證券代號及名稱'].str.split(u' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if u'　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split(u'　')[1]
            df2.iat[i,0]=df2.iat[i,0].split(u'　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:u'公司代號',1:u'股票名稱'})
    del newdf[u'有價證券代號及名稱']

    return newdf

In [14]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_net_income = df_net_income.merge(df_basicinfo, on=u'公司代號', how='inner')

df_net_income

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號      公司名稱  NetIncome(%)_108Q1  NetIncome(%)_107Q4  \
0     1101        台泥               16.68               18.17   
1     1102        亞泥               19.65               17.99   
2     1103        嘉泥               32.84               36.76   
3     1104      環球水泥               13.19               21.99   
4     1108      幸福水泥               -3.57               -6.05   
5     1109      信大水泥               14.89               18.71   
6     1110        東泥                7.15                3.91   
7     1201      味全公司               24.65                4.47   
8     1203      味王公司               12.15               11.58   
9     1210      大成長城                2.75                3.33   
10    1215      卜蜂企業                4.95                4.69   
11    1216        統一                7.26                6.25   
12    1217       愛之味                1.66                1.45   
13    1218      泰山企業                6.10                5.88   
14    1219      福壽實業                0.51               -0.82   
15    1220        台榮                2.46                4.10   
16    1225       福懋油                3.51                2.67   
17    1227        佳格               10.88               10.86   
18    1229      聯華實業               85.47               48.52   
19    1231      聯華食品                5.22                6.67   
20    1232       大統益                7.30                5.47   
21    1233        天仁                7.86                7.97   
22    1234        黑松                7.69                7.82   
23    1235        興泰             -769.70              183.81   
24    1236      宏亞食品                1.73                0.67   
25    1256   鮮活果汁-KY               13.22               13.71   
26    1262     綠悅-KY              -12.74              -11.51   
27    1301        台塑               15.36               21.51   
28    1303      南亞塑膠                7.03               15.81   
29    1304        台聚                4.32                3.08   
30    1305        華夏                5.92                8.93   
31    1307      三芳化工                3.83                3.19   
32    1308        亞聚                8.00                4.50   
33    1309      台達化工                4.24                0.96   
34    1310        台苯               11.18                7.72   
35    1312      國喬石化               11.99               12.73   
36    1313        聯成               -0.92                1.23   
37    1314       中石化                3.80               11.12   
38    1315      達新工業                0.94                9.04   
39    1316        上曜              -33.65               15.22   
40    1319        東陽                8.85                8.40   
41    1321        大洋                3.01               -1.50   
42    1323        永裕                8.30                9.63   
43    1324      地球工業               -1.28                0.11   
44    1325        恒大                5.22                6.55   
45    1326        台化               10.04               13.59   
46    1337     再生-KY              -52.43             -128.92   
47    1338     廣華-KY                5.46                6.13   
48    1339        昭輝               15.76                9.97   
49    1340     勝悅-KY              -11.59                6.50   
50    1402       遠東新                5.56                8.04   
51    1410        南染               15.62               22.01   
52    1413      宏洲纖維                4.27                6.64   
53    1414        東和               -5.60                3.95   
54    1416        廣豐               25.54               92.27   
55    1417        嘉裕              -12.14              -15.57   
56    1418        東華              -49.78              -33.37   
57    1419        新紡               -1.49               17.37   
58    1423      利華羊毛                9.26               13.49   
59    1432     大魯閣實業              -20.23              -21.32   
60    1434      福懋興業                4.79               11.94   
61    1435      中福國際              237.

In [15]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

"""
Export to Excel
Some support is available for exporting styled DataFrames to Excel worksheets using the OpenPyXL or XlsxWriter engines. 
CSS2.2 properties handled include:

* background-color
* border-style, border-width, border-color and their {top, right, bottom, left variants}
* color
* font-family
* font-style
* font-weight
* text-align
* text-decoration
* vertical-align
* white-space: nowrap
"""
def font_family(val):    
    fontfamily = 'Calibri'
    return 'font-family: %s' % fontfamily

def font_size(val):    
    fontsize = '10pt'
    return 'font-size: %s' % fontsize

In [16]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_net_income.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).applymap(font_family).applymap(font_size).to_excel('Styled_Basic_Perspective_NetIncome.xlsx', 'NetIncome_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_108Q1', '2QMAGrowth_108Q1', 'Growth_107Q4', '2QMAGrowth_107Q4', 'Growth_107Q3', '2QMAGrowth_107Q3', 'Growth_107Q2', '2QMAGrowth_107Q2', 'Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2']


C:\ProgramData\Anaconda2\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
